<a href="https://colab.research.google.com/github/Quillbolt/colabnotebook/blob/main/ptlt_trying.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from typing import Tuple

import torch
from torch import nn, Tensor


def convert_label_to_similarity(normed_feature: Tensor, label: Tensor) -> Tuple[Tensor, Tensor]:
    similarity_matrix = normed_feature @ normed_feature.transpose(1, 0)
    label_matrix = label.unsqueeze(1) == label.unsqueeze(0)

    positive_matrix = label_matrix.triu(diagonal=1)
    negative_matrix = label_matrix.logical_not().triu(diagonal=1)

    similarity_matrix = similarity_matrix.view(-1)
    positive_matrix = positive_matrix.view(-1)
    negative_matrix = negative_matrix.view(-1)
    return similarity_matrix[positive_matrix], similarity_matrix[negative_matrix]


class CircleLoss(nn.Module):
    def __init__(self, m: float, gamma: float) -> None:
        super(CircleLoss, self).__init__()
        self.m = m
        self.gamma = gamma
        self.soft_plus = nn.Softplus()

    def forward(self, sp: Tensor, sn: Tensor) -> Tensor:
        ap = torch.clamp_min(- sp.detach() + 1 + self.m, min=0.)
        an = torch.clamp_min(sn.detach() + self.m, min=0.)

        delta_p = 1 - self.m
        delta_n = self.m

        logit_p = - ap * (sp - delta_p) * self.gamma
        logit_n = an * (sn - delta_n) * self.gamma

        loss = self.soft_plus(torch.logsumexp(logit_n, dim=0) + torch.logsumexp(logit_p, dim=0))

        return loss

In [ ]:
    feat = nn.functional.normalize(torch.rand(256, 64, requires_grad=True))
    lbl = torch.randint(high=10, size=(256,))

    inp_sp, inp_sn = convert_label_to_similarity(feat, lbl)

    criterion = CircleLoss(m=0.25, gamma=256)
    circle_loss = criterion(inp_sp, inp_sn)

    print(circle_loss)

tensor(209.7686)


In [ ]:
import torch
from torch import nn, Tensor
from torch.optim import SGD
from torch.utils.data import DataLoader
from torchvision.datasets import MNIST
from torchvision.transforms import ToTensor
from tqdm import tqdm
from torchvision import models

In [ ]:
def get_loader(is_train: bool, batch_size: int) -> DataLoader:
    return DataLoader(
        dataset=MNIST(root="./data", train=is_train, transform=ToTensor(), download=True),
        batch_size=batch_size,
        shuffle=is_train,
    )


In [ ]:
class Model(nn.Module):
    def __init__(self) -> None:
        super(Model, self).__init__()
        self.feature_extractor = nn.Sequential(
            nn.Conv2d(in_channels=1, out_channels=8, kernel_size=5),
            nn.MaxPool2d(kernel_size=2),
            nn.ReLU(),
            nn.Conv2d(in_channels=8, out_channels=16, kernel_size=5),
            nn.MaxPool2d(kernel_size=2),
            nn.ReLU(),
            nn.Conv2d(in_channels=16, out_channels=32, kernel_size=3),
            nn.MaxPool2d(kernel_size=2),
            nn.ReLU(),
        )

    def forward(self, inp: Tensor) -> Tensor:
        feature = self.feature_extractor(inp).mean(dim=[2, 3])
        return nn.functional.normalize(feature)

In [ ]:
model = Model()
optimizer = SGD(model.parameters(), lr=0.001, momentum=0.9, weight_decay=1e-5)
train_loader = get_loader(is_train=True, batch_size=64)
val_loader = get_loader(is_train=False, batch_size=2)
criterion = CircleLoss(m=0.25, gamma=80)

# if resume and os.path.exists("resume.state"):
#     model.load_state_dict(torch.load("resume.state"))
# else:
for epoch in range(20):
    for img, label in tqdm(train_loader):
        model.zero_grad()
        pred = model(img)
        loss = criterion(*convert_label_to_similarity(pred, label))
        loss.requires_grad=True
        loss.backward()
        optimizer.step()
# torch.save(model.state_dict(), "resume.state")

tp = 0
fn = 0
fp = 0
thresh = 0.75
for img, label in val_loader:
    pred = model(img)
    gt_label = label[0] == label[1]
    pred_label = torch.sum(pred[0] * pred[1]) > thresh
    if gt_label and pred_label:
        tp += 1
    elif gt_label and not pred_label:
        fn += 1
    elif not gt_label and pred_label:
        fp += 1

print("Recall: {:.4f}".format(tp / (tp + fn)))
print("Precision: {:.4f}".format(tp / (tp + fp)))


100%|██████████| 938/938 [00:12<00:00, 76.28it/s]


Recall: 1.0000
Precision: 0.0810


In [ ]:
!pip install wandb
!pip install pytorch-lightning

     |████████████████████████████████| 1.8MB 8.5MB/s 
     |████████████████████████████████| 102kB 11.5MB/s 
     |████████████████████████████████| 102kB 11.1MB/s 
     |████████████████████████████████| 163kB 34.7MB/s 
     |████████████████████████████████| 133kB 33.8MB/s 
     |████████████████████████████████| 71kB 9.9MB/s 
  Created wheel for subprocess32: filename=subprocess32-3.5.4-cp36-none-any.whl size=6489 sha256=f97165e96bab4dab89a9efb7392a3d8cc8970452b376a6b02ce74f7c05f95fed
  Stored in directory: /root/.cache/pip/wheels/68/39/1a/5e402bdfdf004af1786c8b853fd92f8c4a04f22aad179654d1
  Created wheel for watchdog: filename=watchdog-1.0.1-cp36-none-any.whl size=72206 sha256=3c336862b8a5a6eca05ba0800e0bab8fc26f4787a87b96c3727bf92029696200
  Stored in directory: /root/.cache/pip/wheels/d8/ce/d8/31a48288b5728794feda5ac479fa324cc1cde4398c29eff064
Successfully built subprocess32 watchdog
     |████████████████████████████████| 675kB 8.1MB/s 
     |████████████████████████████████| 

In [ ]:
import pytorch_lightning as pl
from pytorch_lightning.loggers import WandbLogger
import wandb
wandb.login()
wandb_logger = WandbLogger(project="MNIST")


wandb: Currently logged in as: quillbolt (use `wandb login --relogin` to force relogin)


In [ ]:
class LitClassifier(pl.LightningModule):
    def __init__(self, backbone):
        super().__init__()
        self.save_hyperparameters()
        self.backbone = backbone

    def forward(self, x):
        # use forward for inference/predictions
        embedding = self.backbone(x)
        return embedding

    def training_step(self, batch, batch_idx):
        x, y = batch
        y_hat = self.backbone(x)
        # loss.requires_grad=True
        loss = criterion(*convert_label_to_similarity(y_hat, y))
        self.log('train_loss', loss, on_epoch=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        y_hat = self.backbone(x)
        # loss.requires_grad=True
        loss = criterion(*convert_label_to_similarity(y_hat, y))
        self.log('valid_loss', loss, on_epoch=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        y_hat = self.backbone(x)
        # loss.requires_grad=True
        loss = criterion(*convert_label_to_similarity(y_hat, y))
        self.log('test_loss', loss)

    def configure_optimizers(self):
        # self.hparams available because we called self.save_hyperparameters()
        return torch.optim.SGD(self.parameters(), lr=0.001, momentum=0.9, weight_decay=1e-5)

In [ ]:
train_loader = get_loader(is_train=True, batch_size=64)
val_loader = get_loader(is_train=False, batch_size=2)

Extracting ./data/MNIST/raw/train-images-idx3-ubyte.gz to ./data/MNIST/raw


Extracting ./data/MNIST/raw/train-labels-idx1-ubyte.gz to ./data/MNIST/raw


Extracting ./data/MNIST/raw/t10k-images-idx3-ubyte.gz to ./data/MNIST/raw


Extracting ./data/MNIST/raw/t10k-labels-idx1-ubyte.gz to ./data/MNIST/raw
Processing...
Done!


/usr/local/lib/python3.6/dist-packages/torchvision/datasets/mnist.py:480: UserWarning: The given NumPy array is not writeable, and PyTorch does not support non-writeable tensors. This means you can write to the underlying (supposedly non-writeable) NumPy array using the tensor. You may want to copy the array to protect its data or make it writeable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at  /pytorch/torch/csrc/utils/tensor_numpy.cpp:141.)
  return torch.from_numpy(parsed.astype(m[2], copy=False)).view(*s)


In [ ]:
 model = LitClassifier(Model())
 criterion = CircleLoss(m=0.25, gamma=80)

In [ ]:
 trainer = pl.Trainer(logger=wandb_logger, auto_select_gpus=True,                # use all GPU's
    max_epochs=20)

/usr/local/lib/python3.6/dist-packages/pytorch_lightning/utilities/distributed.py:49: UserWarning: You have set progress_bar_refresh_rate < 20 on Google Colab. This may crash. Consider using progress_bar_refresh_rate >= 20 in Trainer.
  warnings.warn(*args, **kwargs)
GPU available: True, used: False
TPU available: None, using: 0 TPU cores
/usr/local/lib/python3.6/dist-packages/pytorch_lightning/utilities/distributed.py:49: UserWarning: GPU available but not used. Set the --gpus flag when calling the script.
  warnings.warn(*args, **kwargs)


In [ ]:
 trainer.fit(model, train_loader, val_loader)


  | Name     | Type  | Params
-----------------------------------
0 | backbone | Model | 8.1 K 
-----------------------------------
8.1 K     Trainable params
0         Non-trainable params
8.1 K     Total params


wandb: WARNING Step must only increase in log calls.  Step 0 < 899; dropping {'valid_loss_step/epoch_0': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 1 < 899; dropping {'valid_loss_step/epoch_0': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 2 < 899; dropping {'valid_loss_step/epoch_0': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 3 < 899; dropping {'valid_loss_step/epoch_0': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 4 < 899; dropping {'valid_loss_step/epoch_0': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 5 < 899; dropping {'valid_loss_step/epoch_0': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 6 < 899; dropping {'valid_loss_step/epoch_0': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 7 < 899; dropping {'valid_loss_step/epoch_0': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 8 < 899; dropping {'valid_loss_step/epoch_0': 0.0}.
w

Streaming output truncated to the last 5000 lines.
wandb: WARNING Step must only increase in log calls.  Step 20 < 4999; dropping {'valid_loss_step/epoch_1': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 21 < 4999; dropping {'valid_loss_step/epoch_1': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 22 < 4999; dropping {'valid_loss_step/epoch_1': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 23 < 4999; dropping {'valid_loss_step/epoch_1': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 24 < 4999; dropping {'valid_loss_step/epoch_1': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 25 < 4999; dropping {'valid_loss_step/epoch_1': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 26 < 4999; dropping {'valid_loss_step/epoch_1': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 27 < 4999; dropping {'valid_loss_step/epoch_1': 0.0}.
wandb: WARNING Step must only increase in log

Streaming output truncated to the last 5000 lines.
wandb: WARNING Step must only increase in log calls.  Step 20 < 4999; dropping {'valid_loss_step/epoch_2': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 21 < 4999; dropping {'valid_loss_step/epoch_2': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 22 < 4999; dropping {'valid_loss_step/epoch_2': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 23 < 4999; dropping {'valid_loss_step/epoch_2': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 24 < 4999; dropping {'valid_loss_step/epoch_2': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 25 < 4999; dropping {'valid_loss_step/epoch_2': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 26 < 4999; dropping {'valid_loss_step/epoch_2': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 27 < 4999; dropping {'valid_loss_step/epoch_2': 0.0}.
wandb: WARNING Step must only increase in log

Streaming output truncated to the last 5000 lines.
wandb: WARNING Step must only increase in log calls.  Step 19 < 4999; dropping {'valid_loss_step/epoch_3': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 20 < 4999; dropping {'valid_loss_step/epoch_3': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 21 < 4999; dropping {'valid_loss_step/epoch_3': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 22 < 4999; dropping {'valid_loss_step/epoch_3': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 23 < 4999; dropping {'valid_loss_step/epoch_3': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 24 < 4999; dropping {'valid_loss_step/epoch_3': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 25 < 4999; dropping {'valid_loss_step/epoch_3': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 26 < 4999; dropping {'valid_loss_step/epoch_3': 0.0}.
wandb: WARNING Step must only increase in log

...

Streaming output truncated to the last 5000 lines.
wandb: WARNING Step must only increase in log calls.  Step 0 < 5599; dropping {'valid_loss_step/epoch_5': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 1 < 5599; dropping {'valid_loss_step/epoch_5': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 2 < 5599; dropping {'valid_loss_step/epoch_5': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 3 < 5599; dropping {'valid_loss_step/epoch_5': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 4 < 5599; dropping {'valid_loss_step/epoch_5': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 5 < 5599; dropping {'valid_loss_step/epoch_5': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 6 < 5599; dropping {'valid_loss_step/epoch_5': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 7 < 5599; dropping {'valid_loss_step/epoch_5': 0.0}.
wandb: WARNING Step must only increase in log calls. 

Streaming output truncated to the last 5000 lines.
wandb: WARNING Step must only increase in log calls.  Step 0 < 6549; dropping {'valid_loss_step/epoch_6': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 1 < 6549; dropping {'valid_loss_step/epoch_6': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 2 < 6549; dropping {'valid_loss_step/epoch_6': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 3 < 6549; dropping {'valid_loss_step/epoch_6': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 4 < 6549; dropping {'valid_loss_step/epoch_6': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 5 < 6549; dropping {'valid_loss_step/epoch_6': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 6 < 6549; dropping {'valid_loss_step/epoch_6': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 7 < 6549; dropping {'valid_loss_step/epoch_6': 0.0}.
wandb: WARNING Step must only increase in log calls. 

Streaming output truncated to the last 5000 lines.
wandb: WARNING Step must only increase in log calls.  Step 0 < 7499; dropping {'valid_loss_step/epoch_7': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 1 < 7499; dropping {'valid_loss_step/epoch_7': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 2 < 7499; dropping {'valid_loss_step/epoch_7': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 3 < 7499; dropping {'valid_loss_step/epoch_7': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 4 < 7499; dropping {'valid_loss_step/epoch_7': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 5 < 7499; dropping {'valid_loss_step/epoch_7': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 6 < 7499; dropping {'valid_loss_step/epoch_7': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 7 < 7499; dropping {'valid_loss_step/epoch_7': 0.0}.
wandb: WARNING Step must only increase in log calls. 

Streaming output truncated to the last 5000 lines.
wandb: WARNING Step must only increase in log calls.  Step 0 < 8399; dropping {'valid_loss_step/epoch_8': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 1 < 8399; dropping {'valid_loss_step/epoch_8': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 2 < 8399; dropping {'valid_loss_step/epoch_8': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 3 < 8399; dropping {'valid_loss_step/epoch_8': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 4 < 8399; dropping {'valid_loss_step/epoch_8': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 5 < 8399; dropping {'valid_loss_step/epoch_8': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 6 < 8399; dropping {'valid_loss_step/epoch_8': 0.0}.
wandb: WARNING Step must only increase in log calls.  Step 7 < 8399; dropping {'valid_loss_step/epoch_8': 0.0}.
wandb: WARNING Step must only increase in log calls. 

Buffered data was truncated after reaching the output size limit.